# Uniswap V3 Subgraph Liquidity Range Example

This notebook is just the `.ipynb` (for easier reading of both code and output on github) implementation of [this code](https://github.com/atiselsts/uniswap-v3-liquidity-math/blob/master/subgraph-liquidity-range-example.py) (credit: https://github.com/atiselsts) with slight modifications, showing an example on how to query the Uniswap v3 Subgraph for the amounts locked in all ticks with nonzero `liquidityNet` in the USDC/WETH 0.3% pool

See the technical note [Liquidity Math in Uniswap v3](http://atiselsts.github.io/pdfs/uniswap-v3-liquidity-math.pdf), [Uniswap v3 whitepaper](https://uniswap.org/whitepaper-v3.pdf), and [Uniswap V3 Subgraph](https://thegraph.com/legacy-explorer/subgraph/uniswap/uniswap-v3) for more details.

**Library dependency**: The code uses `gql` to query the Uniswap V3 Subgraph API.

In [ ]:
# Example that shows the full range of the current liquidity distribution
# in the 0.3% USDC/ETH pool using data from the Uniswap v3 subgraph.

from gql import gql, Client
from gql.transport.requests import RequestsHTTPTransport
import math

# 0.3% USDC/ETH pool
POOL_ID = "0x8ad599c3a0ff1de082011efddc58f1908eb6e6d8"

# If you want to test with a smaller pool:
# 0.05% GUSD/DAI pool (small pool)
#POOL_ID = "0x7cf12cef5ce9e5e068ebdef470ff8295e26c47b9"

URL = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"

pool_query = """query get_pools($pool_id: ID!) {
  pools(where: {id: $pool_id}) {
    tick
    sqrtPrice
    liquidity
    feeTier
    token0 {
      symbol
      decimals
    }
    token1 {
      symbol
      decimals
    }
  }
}"""

tick_query = """query get_ticks($num_skip: Int, $pool_id: ID!) {
  ticks(skip: $num_skip, where: {pool: $pool_id}) {
    tickIdx
    liquidityNet
  }
}"""

block_query = """query {
  _meta {
    block {
      number
    }
  }
}"""

In [ ]:
TICK_BASE = 1.0001

def tick_to_price(tick):
    return TICK_BASE ** tick

# Not all ticks can be initialized. Tick spacing is determined by the pool's fee tier.
def fee_tier_to_tick_spacing(fee_tier):
    return {
        500: 10,
        3000: 60,
        10000: 200
    }.get(fee_tier, 60)

In [ ]:
client = Client(
    transport=RequestsHTTPTransport(
        url=URL,
        verify=True,
        retries=5,
    ))

In [ ]:
# get current block height, for record
try:
    response = client.execute(gql(block_query))
    blocknum = response['_meta']['block']['number']
    print("Ethereum block height {}".format(blocknum))
except Exception as ex:
    print("got exception", ex)

Ethereum block height 13338973


In [ ]:
# get pool info
try:
    variables = {"pool_id": POOL_ID}
    response = client.execute(gql(pool_query), variable_values=variables)

    if len(response['pools']) == 0:
        print("pool not found")
        exit(-1)

    pool = response['pools'][0]
    current_tick = int(pool["tick"])
    ft = int(pool["feeTier"])
    tick_spacing = fee_tier_to_tick_spacing(ft)

    token0 = pool["token0"]["symbol"]
    token1 = pool["token1"]["symbol"]
    decimals0 = int(pool["token0"]["decimals"])
    decimals1 = int(pool["token1"]["decimals"])
except Exception as ex:
    print("got exception while querying pool data:", ex)
    exit(-1)

pool

{'feeTier': '3000',
 'liquidity': '14035057409658279724',
 'sqrtPrice': '1383050790868526042670137823755671',
 'tick': '195359',
 'token0': {'decimals': '6', 'symbol': 'USDC'},
 'token1': {'decimals': '18', 'symbol': 'WETH'}}

In [ ]:
# get tick info
tick_mapping = {}
num_skip = 0
try:
    while True:
        print("Querying ticks, num_skip={}".format(num_skip))
        variables = {"num_skip": num_skip, "pool_id": POOL_ID}
        response = client.execute(gql(tick_query), variable_values=variables)

        if len(response["ticks"]) == 0:
            break
        num_skip += len(response["ticks"])
        for item in response["ticks"]:
            tick_mapping[int(item["tickIdx"])] = int(item["liquidityNet"])
except Exception as ex:
    print("got exception while querying tick data:", ex)
    exit(-1)

Querying ticks, num_skip=0
Querying ticks, num_skip=100
Querying ticks, num_skip=200
Querying ticks, num_skip=300
Querying ticks, num_skip=400
Querying ticks, num_skip=500
Querying ticks, num_skip=600
Querying ticks, num_skip=700
Querying ticks, num_skip=800
Querying ticks, num_skip=836


In [ ]:
# Start from zero; if we were iterating from the current tick, would start from the pool's total liquidity
liquidity = 0

# Find the boundaries of the price range
min_tick = min(tick_mapping.keys())
max_tick = max(tick_mapping.keys())

# Compute the tick range. This code would work as well in Python: `current_tick // tick_spacing * tick_spacing`
# However, using floor() is more portable.
current_range_bottom_tick = math.floor(current_tick / tick_spacing) * tick_spacing

current_price = tick_to_price(current_tick)
adjusted_current_price = current_price / (10 ** (decimals1 - decimals0))

# Sum up all tokens in the pool
total_amount0 = 0
total_amount1 = 0

# Guess the preferred way to display the price;
# try to print most assets in terms of USD;
# if that fails, try to use the price value that's above 1.0 when adjusted for decimals.
stablecoins = ["USDC", "DAI", "USDT", "TUSD", "LUSD", "BUSD", "GUSD", "UST"]
if token0 in stablecoins and token1 not in stablecoins:
    invert_price = True
elif adjusted_current_price < 1.0:
    invert_price = True
else:
    invert_price = False

# Iterate over the tick map starting from the bottom
tick = min_tick
while tick <= max_tick:
    liquidity_delta = tick_mapping.get(tick, 0)
    liquidity += liquidity_delta
    
    price = tick_to_price(tick)
    adjusted_price = price / (10 ** (decimals1 - decimals0))
    if invert_price:
        adjusted_price = 1 / adjusted_price
        tokens = "{} for {}".format(token0, token1)
    else:
        tokens = "{} for {}".format(token1, token0)

    should_print_tick = liquidity != 0
    if should_print_tick:
        print("ticks=[{}, {}], bottom tick price={:.6g} {}".format(tick, tick + tick_spacing, adjusted_price, tokens))
    
    # Compute square roots of prices corresponding to the bottom and top ticks
    bottom_tick = tick
    top_tick = bottom_tick + tick_spacing
    sa = tick_to_price(bottom_tick // 2)
    sb = tick_to_price(top_tick // 2)
    
    if tick < current_range_bottom_tick:
        # Compute the amounts of tokens potentially in the range
        amount1 = liquidity * (sb - sa) # eq(9) in technical note
        amount0 = amount1 / (sb * sa) # eq(4) and eq(9) in technical note
        
        # Only token1 locked
        total_amount1 += amount1

        if should_print_tick:
            adjusted_amount0 = amount0 / (10 ** decimals0)
            adjusted_amount1 = amount1 / (10 ** decimals1)
            print("        {:.6g} {} locked, potentially worth {:.6g} {}".format(adjusted_amount1, token1, adjusted_amount0, token0))

    elif tick == current_range_bottom_tick:
        # Always print the current tick. It normally has both assets locked
        print("\n        ## Current tick, both assets present!")
        print("        Current price={:.6g} {}".format(1 / adjusted_current_price if invert_price else adjusted_current_price, tokens))

        # Print the real amounts of the two assets needed to be swapped to move out of the current tick range
        current_sqrt_price = tick_to_price(current_tick / 2)
        amount0actual = liquidity * (sb - current_sqrt_price) / (current_sqrt_price * sb) # eq(12) in technical note
        amount1actual = liquidity * (current_sqrt_price - sa) # eq(13) in technical note
        adjusted_amount0actual = amount0actual / (10 ** decimals0)
        adjusted_amount1actual = amount1actual / (10 ** decimals1)
        
        total_amount0 += amount0actual
        total_amount1 += amount1actual

        print("        {:.6g} {} and {:.6g} {} remaining in the current tick range\n".format(
            adjusted_amount0actual, token0, adjusted_amount1actual, token1))        
        
    else:
        # Compute the amounts of tokens potentially in the range
        amount1 = liquidity * (sb - sa)
        amount0 = amount1 / (sb * sa)

        # Only token0 locked
        total_amount0 += amount0

        if should_print_tick:
            adjusted_amount0 = amount0 / (10 ** decimals0)
            adjusted_amount1 = amount1 / (10 ** decimals1)
            print("        {:.6g} {} locked, potentially worth {:.6g} {}".format(adjusted_amount0, token0, adjusted_amount1, token1))

    tick += tick_spacing

print("\nIn total: {:.6g} {} and {:.6g} {} (not including accrued swap fees)".format(
      total_amount0 / (10 ** decimals0), token0, total_amount1 / (10 ** decimals1), token1))

current_adjusted_price = tick_to_price(current_tick) / (10 ** (decimals1 - decimals0))
print("At current price {:.6g} {} for 1 {} ({:.6g} {} for 1 {}),".format(
    current_adjusted_price, token1, token0, 1 / current_adjusted_price, token0, token1))

print("  equiv. to total liquidity {:.6g} {} or {:.6g} {}".format(
    (total_amount1/current_price+total_amount0)/(10**decimals0), token0,(total_amount0*current_price+total_amount1)/(10**decimals1),token1))
print("As at Ethereum block height {}".format(blocknum))

ticks=[-887220, -887160], bottom tick price=3.38492e+50 USDC for WETH
        5.76219e-25 WETH locked, potentially worth 1.94461e+26 USDC
ticks=[-887160, -887100], bottom tick price=3.36467e+50 USDC for WETH
        5.94108e-25 WETH locked, potentially worth 1.99299e+26 USDC
ticks=[-887100, -887040], bottom tick price=3.34455e+50 USDC for WETH
        5.95893e-25 WETH locked, potentially worth 1.98702e+26 USDC
ticks=[-887040, -886980], bottom tick price=3.32454e+50 USDC for WETH
        5.97683e-25 WETH locked, potentially worth 1.98107e+26 USDC
ticks=[-886980, -886920], bottom tick price=3.30465e+50 USDC for WETH
        5.99479e-25 WETH locked, potentially worth 1.97514e+26 USDC
ticks=[-886920, -886860], bottom tick price=3.28489e+50 USDC for WETH
        6.0128e-25 WETH locked, potentially worth 1.96922e+26 USDC
ticks=[-886860, -886800], bottom tick price=3.26524e+50 USDC for WETH
        6.03086e-25 WETH locked, potentially worth 1.96332e+26 USDC
ticks=[-886800, -886740], bottom ti

        3.839e-24 WETH locked, potentially worth 3.08427e+25 USDC
ticks=[-849780, -849720], bottom tick price=8.00998e+48 USDC for WETH
        3.85054e-24 WETH locked, potentially worth 3.07503e+25 USDC
ticks=[-849720, -849660], bottom tick price=7.96206e+48 USDC for WETH
        3.8621e-24 WETH locked, potentially worth 3.06582e+25 USDC
ticks=[-849660, -849600], bottom tick price=7.91444e+48 USDC for WETH
        3.87371e-24 WETH locked, potentially worth 3.05664e+25 USDC
ticks=[-849600, -849540], bottom tick price=7.8671e+48 USDC for WETH
        3.88535e-24 WETH locked, potentially worth 3.04748e+25 USDC
ticks=[-849540, -849480], bottom tick price=7.82004e+48 USDC for WETH
        3.89702e-24 WETH locked, potentially worth 3.03835e+25 USDC
ticks=[-849480, -849420], bottom tick price=7.77326e+48 USDC for WETH
        3.90873e-24 WETH locked, potentially worth 3.02925e+25 USDC
ticks=[-849420, -849360], bottom tick price=7.72676e+48 USDC for WETH
        3.92047e-24 WETH locked, poten

        1.72039e-23 WETH locked, potentially worth 6.88245e+24 USDC
ticks=[-819780, -819720], bottom tick price=3.98853e+47 USDC for WETH
        1.72556e-23 WETH locked, potentially worth 6.86184e+24 USDC
ticks=[-819720, -819660], bottom tick price=3.96467e+47 USDC for WETH
        1.73075e-23 WETH locked, potentially worth 6.84129e+24 USDC
ticks=[-819660, -819600], bottom tick price=3.94096e+47 USDC for WETH
        1.73595e-23 WETH locked, potentially worth 6.82079e+24 USDC
ticks=[-819600, -819540], bottom tick price=3.91738e+47 USDC for WETH
        1.74116e-23 WETH locked, potentially worth 6.80036e+24 USDC
ticks=[-819540, -819480], bottom tick price=3.89395e+47 USDC for WETH
        1.74639e-23 WETH locked, potentially worth 6.77999e+24 USDC
ticks=[-819480, -819420], bottom tick price=3.87066e+47 USDC for WETH
        1.75164e-23 WETH locked, potentially worth 6.75968e+24 USDC
ticks=[-819420, -819360], bottom tick price=3.84751e+47 USDC for WETH
        1.7569e-23 WETH locked, po

ticks=[-789840, -789780], bottom tick price=1.99802e+46 USDC for WETH
        7.70969e-23 WETH locked, potentially worth 1.5358e+24 USDC
ticks=[-789780, -789720], bottom tick price=1.98607e+46 USDC for WETH
        7.73285e-23 WETH locked, potentially worth 1.5312e+24 USDC
ticks=[-789720, -789660], bottom tick price=1.97419e+46 USDC for WETH
        7.75608e-23 WETH locked, potentially worth 1.52661e+24 USDC
ticks=[-789660, -789600], bottom tick price=1.96238e+46 USDC for WETH
        7.77938e-23 WETH locked, potentially worth 1.52204e+24 USDC
ticks=[-789600, -789540], bottom tick price=1.95064e+46 USDC for WETH
        7.80275e-23 WETH locked, potentially worth 1.51748e+24 USDC
ticks=[-789540, -789480], bottom tick price=1.93897e+46 USDC for WETH
        7.8262e-23 WETH locked, potentially worth 1.51293e+24 USDC
ticks=[-789480, -789420], bottom tick price=1.92738e+46 USDC for WETH
        7.84971e-23 WETH locked, potentially worth 1.5084e+24 USDC
ticks=[-789420, -789360], bottom tick 

ticks=[-759840, -759780], bottom tick price=9.94906e+44 USDC for WETH
        3.45498e-22 WETH locked, potentially worth 3.42709e+23 USDC
ticks=[-759780, -759720], bottom tick price=9.88955e+44 USDC for WETH
        3.46536e-22 WETH locked, potentially worth 3.41682e+23 USDC
ticks=[-759720, -759660], bottom tick price=9.83039e+44 USDC for WETH
        3.47577e-22 WETH locked, potentially worth 3.40659e+23 USDC
ticks=[-759660, -759600], bottom tick price=9.77159e+44 USDC for WETH
        3.48622e-22 WETH locked, potentially worth 3.39638e+23 USDC
ticks=[-759600, -759540], bottom tick price=9.71314e+44 USDC for WETH
        3.49669e-22 WETH locked, potentially worth 3.38621e+23 USDC
ticks=[-759540, -759480], bottom tick price=9.65504e+44 USDC for WETH
        3.5072e-22 WETH locked, potentially worth 3.37607e+23 USDC
ticks=[-759480, -759420], bottom tick price=9.59728e+44 USDC for WETH
        3.51773e-22 WETH locked, potentially worth 3.36595e+23 USDC
ticks=[-759420, -759360], bottom ti

...

ticks=[746280, 746340], bottom tick price=3.90024e-21 USDC for WETH
        6.66811e-10 USDC locked, potentially worth 1.7148e+11 WETH
ticks=[746340, 746400], bottom tick price=3.87691e-21 USDC for WETH
        6.64814e-10 USDC locked, potentially worth 1.71995e+11 WETH
ticks=[746400, 746460], bottom tick price=3.85372e-21 USDC for WETH
        6.62823e-10 USDC locked, potentially worth 1.72512e+11 WETH
ticks=[746460, 746520], bottom tick price=3.83067e-21 USDC for WETH
        6.60837e-10 USDC locked, potentially worth 1.7303e+11 WETH
ticks=[746520, 746580], bottom tick price=3.80776e-21 USDC for WETH
        6.58858e-10 USDC locked, potentially worth 1.7355e+11 WETH
ticks=[746580, 746640], bottom tick price=3.78498e-21 USDC for WETH
        6.56884e-10 USDC locked, potentially worth 1.74072e+11 WETH
ticks=[746640, 746700], bottom tick price=3.76234e-21 USDC for WETH
        6.54917e-10 USDC locked, potentially worth 1.74595e+11 WETH
ticks=[746700, 746760], bottom tick price=3.73983e-

        1.69284e-10 USDC locked, potentially worth 6.75464e+11 WETH
ticks=[773760, 773820], bottom tick price=2.49868e-22 USDC for WETH
        1.68777e-10 USDC locked, potentially worth 6.77493e+11 WETH
ticks=[773820, 773880], bottom tick price=2.48373e-22 USDC for WETH
        1.68271e-10 USDC locked, potentially worth 6.79528e+11 WETH
ticks=[773880, 773940], bottom tick price=2.46887e-22 USDC for WETH
        1.67767e-10 USDC locked, potentially worth 6.8157e+11 WETH
ticks=[773940, 774000], bottom tick price=2.45411e-22 USDC for WETH
        1.67265e-10 USDC locked, potentially worth 6.83618e+11 WETH
ticks=[774000, 774060], bottom tick price=2.43943e-22 USDC for WETH
        1.66763e-10 USDC locked, potentially worth 6.85671e+11 WETH
ticks=[774060, 774120], bottom tick price=2.42483e-22 USDC for WETH
        1.66264e-10 USDC locked, potentially worth 6.87731e+11 WETH
ticks=[774120, 774180], bottom tick price=2.41033e-22 USDC for WETH
        1.65766e-10 USDC locked, potentially wort

ticks=[805800, 805860], bottom tick price=1.01461e-23 USDC for WETH
        3.401e-11 USDC locked, potentially worth 3.36209e+12 WETH
ticks=[805860, 805920], bottom tick price=1.00854e-23 USDC for WETH
        3.39082e-11 USDC locked, potentially worth 3.37219e+12 WETH
ticks=[805920, 805980], bottom tick price=1.00251e-23 USDC for WETH
        3.38066e-11 USDC locked, potentially worth 3.38233e+12 WETH
ticks=[805980, 806040], bottom tick price=9.96514e-24 USDC for WETH
        3.37053e-11 USDC locked, potentially worth 3.39249e+12 WETH
ticks=[806040, 806100], bottom tick price=9.90553e-24 USDC for WETH
        3.36044e-11 USDC locked, potentially worth 3.40268e+12 WETH
ticks=[806100, 806160], bottom tick price=9.84628e-24 USDC for WETH
        3.35037e-11 USDC locked, potentially worth 3.4129e+12 WETH
ticks=[806160, 806220], bottom tick price=9.78738e-24 USDC for WETH
        3.34034e-11 USDC locked, potentially worth 3.42316e+12 WETH
ticks=[806220, 806280], bottom tick price=9.72884e-

        7.77357e-12 USDC locked, potentially worth 1.47094e+13 WETH
ticks=[835380, 835440], bottom tick price=5.26892e-25 USDC for WETH
        7.75029e-12 USDC locked, potentially worth 1.47536e+13 WETH
ticks=[835440, 835500], bottom tick price=5.2374e-25 USDC for WETH
        7.72707e-12 USDC locked, potentially worth 1.4798e+13 WETH
ticks=[835500, 835560], bottom tick price=5.20607e-25 USDC for WETH
        7.70393e-12 USDC locked, potentially worth 1.48424e+13 WETH
ticks=[835560, 835620], bottom tick price=5.17493e-25 USDC for WETH
        7.68085e-12 USDC locked, potentially worth 1.4887e+13 WETH
ticks=[835620, 835680], bottom tick price=5.14398e-25 USDC for WETH
        7.65785e-12 USDC locked, potentially worth 1.49317e+13 WETH
ticks=[835680, 835740], bottom tick price=5.11321e-25 USDC for WETH
        7.63491e-12 USDC locked, potentially worth 1.49766e+13 WETH
ticks=[835740, 835800], bottom tick price=5.08262e-25 USDC for WETH
        7.61204e-12 USDC locked, potentially worth 

ticks=[871980, 872040], bottom tick price=1.35607e-26 USDC for WETH
        1.24337e-12 USDC locked, potentially worth 9.19641e+13 WETH
ticks=[872040, 872100], bottom tick price=1.34796e-26 USDC for WETH
        1.23964e-12 USDC locked, potentially worth 9.22404e+13 WETH
ticks=[872100, 872160], bottom tick price=1.3399e-26 USDC for WETH
        1.23593e-12 USDC locked, potentially worth 9.25175e+13 WETH
ticks=[872160, 872220], bottom tick price=1.33188e-26 USDC for WETH
        1.23223e-12 USDC locked, potentially worth 9.27955e+13 WETH
ticks=[872220, 872280], bottom tick price=1.32392e-26 USDC for WETH
        1.22853e-12 USDC locked, potentially worth 9.30743e+13 WETH
ticks=[872280, 872340], bottom tick price=1.316e-26 USDC for WETH
        1.22485e-12 USDC locked, potentially worth 9.33539e+13 WETH
ticks=[872340, 872400], bottom tick price=1.30813e-26 USDC for WETH
        1.22119e-12 USDC locked, potentially worth 9.36344e+13 WETH
ticks=[872400, 872460], bottom tick price=1.3003e-2